In [585]:
# # -*- coding: utf-8 -*-
# from ckiptagger import data_utils # first use ckip, need to download data file
# data_utils.download_data_gdown("./")
from ckiptagger import WS, POS, NER, construct_dictionary

ws = WS("./ckip_data") # word segment
# pos = POS("./ckip_data") 
# ner = NER("./ckip_data") # entity recognition

import os
import csv
import pandas as pd
import numpy as np
import time
import math
import re
import demoji
from collections import Counter # count most common word
# demoji.download_codes()


#====== import jieba dict =====
import jieba
jieba.set_dictionary('dataset/dic_trad/dict.txt.big')
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt')


#====== selenium activate esc key ======
from selenium.webdriver import ActionChains # activate esc key
from selenium.webdriver.common.keys import Keys # activate esc key

#====== selenium cathc NoSuchElementException ======
from selenium.common.exceptions import NoSuchElementException   
def check_exists_by_xpath(xpath):
    try:
        driver.find_element_by_xpath(xpath)
    except NoSuchElementException:
        return False
    return True

#====== evaluation metrics ======
from sklearn.metrics import mean_squared_error #均方誤差
from sklearn.metrics import mean_absolute_error as mae #平方絕對誤差
from sklearn.metrics import r2_score

#====== MSE ======
def MSE(y, y_pred):
 
    mse = np.mean((y - y_pred)**2)
   
    return mse

Building prefix dict from /home/alvin/essay/dataset/dic_trad/dict.txt.big ...
Loading model from cache /tmp/jieba.ucbd952ca8a83da26cb61ea55c46a2e3b.cache
Loading model cost 1.237 seconds.
Prefix dict has been built successfully.


In [274]:
def load_new_jeiba_word():
    jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict

In [629]:
#====== get antusd senti dict ======
colNames = ['Word','Score','Pos','Neu','Neg','Non','Not']
antusd = pd.read_csv('dataset/ANTUSD_traditional/opinion_word.csv', names = colNames) 

#====== drop 0 score of antusd ======
# drop_index_list = list(antusd[antusd['Score'] == 0].index)
# antusd = antusd.drop(drop_index_list) # 20806 senti word (after remvoe zero score)

# combine word & score
word_senti_score = dict(zip(antusd['Word'],antusd['Score'])) # find score via word, 27221 senti words

print(len(antusd))
print(len(word_senti_score))

28799
27221


In [832]:
#====== emoji_sentiment_dict ======
def read_emoji_csv():
    emoji_sentiment = pd.read_csv('dataset/dic_trad/Emoji_Sentiment.csv') # read Emoji_Sentiment.csv
    emoji_sentiment.drop(columns=['Unnamed: 0'], inplace = True)
    emoji_sentiment_dict = dict(zip(emoji_sentiment['Emoji'],emoji_sentiment['Sentiment score'])) # key,value
    return emoji_sentiment_dict

emoji_sentiment_dict = read_emoji_csv()

In [639]:
#====== read new_antusd_word_senti ======
def read_new_antusd_senti(filename):
    new_antusd_pos_word_senti_dict = {}
    with open(filename, newline='') as f: # open in readonly mode
            rows = csv.reader(f)
            for row in rows:
                word = row[0]
                score = float(row[1])
                if word not in new_antusd_pos_word_senti_dict:
                    new_antusd_pos_word_senti_dict[word] = score
    return new_antusd_pos_word_senti_dict
                    
    



In [5]:
def get_selenium_param(filename):
    paramList = []
    with open("dataset/ig_article/"+filename, "r") as f:
        for line in f:
            single_store_param = line.split(',')
            single_store_param[2] = single_store_param[2].replace('\n','')
            paramList.append(single_store_param)

    return paramList

In [6]:
#====== data preprocess - related function ======
def get_store_names(food_kind):
    store_names = [food_kind]
    # read ranked store names
    with open("dataset/ig_article/store_article/"+food_kind+"/ranked_store_names", "r") as f:    
        for line in f:
            store_names.append(line.strip())
        
    return store_names
    
def get_remove_word():
    word_list = []
    with open("dataset/dic_trad/removed_word.txt", "r") as f:    
        for line in f:
            word_list.append(line.strip())
        
    return word_list

In [640]:
#====== extend senti. dict (manual add single word)======
def self_extend_senti_dict(word_senti_score):
    with open("dataset/dic_trad/extend_senti_score_dict.txt", "r") as f:
        for line in f:
            senti_word = line.split()[0]
            senti_score = float(line.split()[1])
            word_senti_score[senti_word] = senti_score


#====== extend hotpot senti. dict ======
def self_extend_senti_dict_hotpot(word_senti_score):
    with open("dataset/dic_trad/extend_senti_score_dict_hotpot.txt", "r") as f:
        for line in f:
            senti_word = line.split()[0]
            senti_score = float(line.split()[1])
            word_senti_score[senti_word] = senti_score    
            
# #====== extend manual marking anutsd senti. dict ======
def add_new_antusd_senti_score(word_senti_score, new_antusd_word_senti):
    word_senti_score.update(new_antusd_word_senti)

        
#====== add emoji senti score ======
def add_emoji_senti_score(word_senti_score, emoji_sentiment_dict):
    word_senti_score.update(emoji_sentiment_dict)
#     return word_senti_score




In [833]:
print(len(word_senti_score))
word_senti_score['💗']

28423


0.657

In [834]:
len(emoji_sentiment_dict)

751

In [9]:
print(len(word_senti_score),len(emoji_sentiment_dict))

28107 751


In [ ]:
#====== test ckip word segment ======

# text = '傅達仁今將執行安樂死，卻突然爆出自己20年前遭緯來體育台封殺，他不懂自己哪裡得罪到電視台。'
# text = '"鬼金棒，我就跟！就這樣，我又跟我的前衣食父母吃飯！連吃兩天拉麵🍜一個胖的節奏#鬼金棒拉麵#辣正常麻增量#結果真的麻到我頭皮發麻 我到底要不要改機票呢😏"'
# text = '期盼那麼久才吃到，果然不負期望，無論是湯頭還是肉片都是最佳狀態，太享受了'
text = '好久不見！，體力一年不如一年，#20191101，服務態度超優的，海鮮😋,海底撈圈字遊戲送一盤肉,👍👍👍撈撈撈，💋💋💋,排隊排好久 超值得, 我要再來刷二訪 😋， 以愛吃重口味的我來說 麵條的硬度很讚 乾, 想吃很膩害的溏心蛋 這家沾麵真的很優,湯頭也很濃 我不愛沾麵 難波萬台灣美食成為我的愛店之一👍🏻好多人，不知道要排多久,麻的味道超級棒,推推推,湯頭還是很棒，豆芽菜的鑊氣沒了很難過，大概一陣子不會回訪了,good excelent,熱死第一名,可惜還是沒把湯喝完,應該很普通,不是我的最愛。'


ws_results = ws([text])
# pos_results = pos(ws_results)
# ner_results = ner(ws_results, pos_results)

print(ws_results)
# print(pos_results)
# for name in ner_results[0]:# print entity
#     print(name)

In [6]:
# word_pos = dict(zip(ws_results[0],pos_results[0])) # combine word and pos tag

In [1052]:
#====== data preprocess - implementation ======
def data_preprocess(articles): 
    # only get string comment & preprocess fans, likes
    all_comments, assigned_index, fans_count, likes  = [],[],[],[]  # assigned_index: denote the original dataframe index of comments
    for i in range(len(articles['text'])):     # remove '\n'
        if type(articles['text'][i]) == str:   # remove non-string
            
            # exclude noise article(ex:染髮)
            temp_word_list = jieba.lcut(articles['text'][i])
            remove_flag = False
            for removed_word in get_remove_word():
                if removed_word in temp_word_list:
                    remove_flag = True
                    break
            if remove_flag:
                continue
                    
            # if contain '\n', replace with ','
            if articles['text'][i].find('\n'): 
                all_comments.append(articles['text'][i].replace('\n','，').upper()) # remove '\n', make upper case
            else:
                all_comments.append(articles['text'][i].upper())
            assigned_index.append(i)
            
#             # get assigned fans_count
#             if type(articles['fans_count'][i]) == np.float64 and math.isnan(articles['fans_count'][i]):
#                 fans_count.append(0)
#             elif type(articles['fans_count'][i]) == np.float64 and np.isnan(articles['fans_count'][i]):
#                 fans_count.append(0)
#             elif str(articles['fans_count'][i]).find('萬') != -1:
#                 wan_index = articles['fans_count'][i].find('萬')
#                 transform_count = (float(articles['fans_count'][i][:wan_index])) * 10000
#                 fans_count.append(transform_count)
#             else:
#                 fans_count.append(int(articles['fans_count'][i]))
            fans_count = []


            # get assigned likes
            temp_like = articles['likes'][i]
            if type(temp_like) == np.float64 or type(temp_like) == np.int64:
                likes.append(temp_like)
            elif type(temp_like) == str:
                if temp_like.isdigit():
                    likes.append(float(temp_like))
                else:
                    likes.append(1)
            else:
                likes.append(temp_like)
            
        # get article at most 120 post
        if len(all_comments) == 150:
            break
    
    return all_comments, assigned_index, fans_count, likes

In [464]:
#====== cal senti score by jieba ======
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict
    
def get_senti_score(text, print_comment):
    '''calculate one sentence's score'''
    if print_comment:
        ws_results = [jieba.lcut(text)] # word segment
        # get sentiword in dict
        total_score = 0
        for word in ws_results[0]:
            if word in word_senti_score:
                score = word_senti_score[word]
                total_score += score 
                print(word,score) # print each senti word's senti score
        print('sent_score:',total_score)

    else:                               # not print one sentence total score
        ws_results = [jieba.lcut(text)] # word segment
        # get sentiword in dict
        total_score = 0
        for word in ws_results[0]:
            if word in word_senti_score:
                score = word_senti_score[word]
                total_score += score 

    
    return total_score

In [ ]:
#====== cal senti score by ckip ======
# def get_senti_score(text):
#     ws_results = ws([text]) # word segment
#     total_score = 0
#     for word in ws_results[0]:
#         if word in word_senti_score:
#             score = word_senti_score[word]
#             total_score += score 
#             print(word,score) # print each senti word's senti score
    
    
#     print('sent_score:',total_score)
#     if total_score >= 1:
#         return 1
#     elif total_score <= -1:
#         return -1
#     else:
#         return total_score

In [1217]:
#====== get each comment's score ======
def get_each_comment_score(all_comments, print_comment):
    all_comments_scores = []
    if print_comment:
        for i,single_comment in enumerate(all_comments):
            print('\n['+str(i)+']'+'comment:',single_comment)
            all_comments_scores.append(get_senti_score(single_comment, print_comment))
    else:
        for single_comment in all_comments:
            all_comments_scores.append(get_senti_score(single_comment, print_comment))
        
    return all_comments_scores

In [15]:
#====== cal store score ======      # not yet consider no comment post's effect (maybe effective) 
def get_store_score(weight, each_comment_score, assigned_index):
    '''store score = comment score * likes(weight) /all likes'''
    weighted_score = 0
    total_weight = 0
    for i in range(len(each_comment_score)):
        if not np.isnan(weight[i]):
            weighted_score += (weight[i] * each_comment_score[i])
            total_weight += weight[i] 
            
    store_score = weighted_score / total_weight

    return store_score


In [18]:
def output_csv(filename, data_list, write_method):

    import csv

    # 開啟輸出的 CSV 檔案
    with open(filename, write_method, newline='') as csvfile:
        writer  = csv.writer(csvfile)   # 建立 CSV 檔寫入器
        for row in data_list: # format: two dimension
            writer.writerow(row)
            

In [ ]:
#====== remove foreign language post ======
# for i,content in zip(articles[articles['text'].notnull()]['text'].index,
#                      articles[articles['text'].notnull()]['text']):
#     if not re.search(r'[\u4e00-\u9fff]+', content) and not demoji.findall(content): # check contain chinese
#         print(i,content)
#         # drop assigned row
#         articles.drop(i, inplace=True) 
        
# # reset dataframe index
# articles.reset_index(drop=True) 

In [19]:
text = '這是一場五感都被放大的饗宴。﻿，﻿，有硬度及Q勁的麵體，🐠很喜歡，搭配辣少麻少的濃厚湯頭，非常過癮！鬼金棒的辣和麻是一流的，入口先感受到辣，隨之而來的麻會讓你感受到舌尖的震顫，建議第一次吃、不是很敢吃麻辣的朋友跟🐠一樣選擇辣少麻少。﻿，﻿，鬼金棒的拉麵，就是這樣強勁有力。﻿，﻿，叉燒肉也和大多數的拉麵店不同，選用大塊的五花肉，乍看之下有點像控肉（但絕對不是），肥瘦相間、軟嫩好入口，有別於一般薄片叉燒，鬼金棒就是這樣的霸氣！﻿，﻿，最後額外提一下，店裡的冰開水不知道為什麼，特別甘甜好喝啊🤣﻿，﻿，﻿，-·-·-·-·-·-﻿，🔺用餐請遵守店內顧客須知，大家一起當優良好客人！﻿，🔺吃完麵再加白飯100分！但麵的份量本身就蠻大了，要自己斟酌哦！﻿，——————————，﻿，🌟如果喜歡濃厚拉麵，或者吃膩了一般口味的拉麵，來鬼金棒走一遭吧☺️﻿，﻿，——————————，🏠辣麻味噌拉麵 鬼金棒﻿，📍104台北市中山區長安西路19巷2弄35號（近捷運中山站）﻿，🕐平日11:30-14:00/17:00-20:30，假日11:30-20:30﻿，，#辣麻味噌拉麵 #鬼金棒 #鬼金棒カラシビ味噌ラーメン #拉麵 #叉燒肉 #捷運美食 #捷運中山站 #ramen #ramennoodles 當然是想到鬼金棒💕，麻的味道超級棒，讓你一口接一口🤤，肉的份量也很足👍，湯頭非常濃郁‼️，吃#nightmarket #taiwan #taipei #noodles #stinkytofu 🤤#squid #seafood #dumplings #ningxia #nightlife,豪豪ㄘ 嘴唇超麻～～～,敲好ㄘ🌶🌶🌶🌶🍜'

# print(ws([text]))
demoji.findall(text)
for emoji in demoji.findall(text):
    if emoji_sentiment_dict.get(emoji):
        print(emoji,emoji_sentiment_dict[emoji])

🏠 0.5
👍 0.521
📍 0.111
🐠 0.414
🌟 0.327
🍜 0.395
💕 0.632


In [ ]:
jieba.lcut('新娘美甲喝起來更香濃愛吃重口味的我來說嗚嗚嗚嗚可惜吃到後面有點膩今天沾麵日！白湯&海湯沾麵🍜')

In [433]:
#======evaluation: read other rank method ======
def read_other_rank(food_kind):
    rank_dict = {'google':{},'ifoodie':{}}
#     food_kind = ['pasta','hotpot','ramen','beef_noodle','pork_rice']
    with open("dataset/ig_article/store_article/other_rank_method",'r') as file:
        for line in file:
            if line.find('google') != -1:        # not found, return -1
                for food in food_kind:
                    if line.find(food) != -1:     # ex:find google pasta rank
                        str_rank_list = line.strip().split(':')[1].split(',')
                        rank_dict['google'][food] = [int(i) for i in str_rank_list]
                        break
                    
                    
                    
#                 if line.find('pasta') != -1:     # find google pasta rank
#                     str_rank_list = line.strip().split(':')[1].split(',')
#                     rank_dict['google']['pasta'] = [int(i) for i in str_rank_list]
                
#                 elif line.find('hotpot') != -1:   # find google pasta rank
#                     str_rank_list = line.strip().split(':')[1].split(',')
#                     rank_dict['google']['hotpot'] = [int(i) for i in str_rank_list]
                
#                 elif line.find('ramen') != -1:   # find google pasta rank
#                     str_rank_list = line.strip().split(':')[1].split(',')
#                     rank_dict['google']['ramen'] = [int(i) for i in str_rank_list]
                    
            elif line.find('ifoodie') != -1:
#                 if line.find('pasta') != -1:
#                     str_rank_list = line.strip().split(':')[1].split(',')
#                     rank_dict['ifoodie']['pasta'] = [int(i) for i in str_rank_list]
                for food in food_kind:
                    if line.find(food) != -1:     # ex:find google pasta rank
                        str_rank_list = line.strip().split(':')[1].split(',')
                        rank_dict['ifoodie'][food] = [int(i) for i in str_rank_list]
                        break    
                    
                    
        
    return rank_dict
            


In [162]:
#====== choose food kind to get mse ======
def get_evaluation_result(food_kind, rank_dict, new_rating_score, store_names, all_store_post_count):
    print('\n===================== '+ food_kind +' rank =====================')
    store_rank = []
    temp_rating = new_rating_score[:]
    temp_rating.sort(reverse = True)
    cnt = 1
    for name,i in zip(store_names[1:],new_rating_score):
        rank = temp_rating.index(i)+1
        store_rank.append(rank)
        print('第'+str(cnt)+'名:',name,round(i,5),',',all_store_post_count[cnt-1],'post',',',rank)
        cnt += 1


    new_mse = MSE(np.array(range(1,11)),np.array(store_rank))
    print('\n新評分機制排名:',store_rank)
    print('MSE:',new_mse)
    print('r2_score:',round(r2_score(np.array(range(1,11)),np.array(store_rank)),3))
    print('--------------------Google--------------------')
    print('Google_rank: ' + str(rank_dict['google'][food_kind]))
    print('Google_MSE:',MSE(np.array(range(1,11)),np.array(rank_dict['google'][food_kind])))
    print('Google_r2_score:',round(r2_score(np.array(range(1,11)),np.array(rank_dict['google'][food_kind])),3))
    print('--------------------ifoodie--------------------')
    print('ifoodie_rank: ' + str(rank_dict['ifoodie'][food_kind]))
    print('ifoodie_MSE:',MSE(np.array(range(1,11)),np.array(rank_dict['ifoodie'][food_kind])))
    print('ifoodie_r2_score:',round(r2_score(np.array(range(1,11)),np.array(rank_dict['ifoodie'][food_kind])),3))
    return new_mse

# Cal one store rating

In [173]:
def norm_score_1(all_comments_scores):
    '''bigger or less than 1/-1 => 1/-1'''
    norm_all_comments_scores = []
    for one_score in all_comments_scores:
        if one_score >= 1:
            norm_all_comments_scores.append(1)
        elif one_score <= -1:
            norm_all_comments_scores.append(-1)
        else:
            norm_all_comments_scores.append(one_score)

    return norm_all_comments_scores

def norm_score_2(x):
    '''max_min norm to [-1,1]'''
    return [(float(i)-np.mean(x))/(max(x)-min(x)) for i in x]

def max_min_normalization(x):
    '''max_min norm to [0,1]'''
    return [(float(i)-min(x))/float(max(x)-min(x)) for i in x]

In [783]:
for i in articles['text']:
    print('\ncontent:')
    print(i)


content:
🤨
忙碌一個早上，放空一個下午 🐣
#tainan #台南 #kaffeathome

content:
熱情赴約🌹寶貝 努力的女人最美喔🌹

content:
想再來第二次的店❤️🤤

content:
天灰灰的 
休假用餐時間
享受餐館裡的優雅時刻～
#藍莓香蕉牛奶#奶油蘑菇雞肉脆片
#義大利#餐後甜點#起士布朗尼 #天灰灰#張開眼睛就在吃#吃貨

content:
#奶油蘑菇雞肉脆餅
#茄汁鴨胸烤培根
#奶油牛肉香料蕈菇
#綜合野莓起司巧克力
#起司布朗尼
#檸檬巧克力塔
#home奶茶
#檸香冰茶
#kaffeathome
#食

content:
nan

content:
Sleep and rest is overrated

content:
#kaffeathome 
平價好吃，藏在巷子內的放鬆好去處
-
👀左滑有菜單
-
🌮奶油牛肉香料蕈菇義大利碗麵 190
料還蠻多的，滿滿的蕈菇乾跟牛肉，還有一些櫛瓜，牛肉帶點筋，煮得口感非常軟嫩，麵體頗彈牙，蕈菇跟奶油白醬的香氣都非常濃郁，而且醬料的量非常夠，全部搭配著一起吃超滿足
-
🌮茄汁鴨胸烤培根義大利碗麵 190
上一道走濃郁路線，這道走清爽路線
鴨胸帶點微微煙燻香氣，肉質Q彈，鹹香夠味，搭配一些培根、櫛瓜還有甜椒，夠量的茄汁酸甜開胃，一下就完食了
-
🌮時尚布朗尼 100
這道超好吃，加熱過的起司巧克力布朗尼，搭配一球口感綿密濃郁的香草冰淇淋跟甜杏仁脆片，超銷魂
-
🌮草莓雲朵 120
外型很夢幻，口味上就中規中矩的草莓冰砂
-
🌮拿鐵咖啡 110
就一般還不錯喝的拿鐵
-
⛱裝潢文青，採光好，冷氣也很涼，非常舒適放鬆的用餐環境
-
🕑營業時間 11:00-21:00
-
📮地址 台南市東區大學路22巷3號
-
🎈歡迎追蹤IG @little.a.foodie.tw 🍡🍡🍡
-
🔎#AA吃台南
-
#台南美食 #台南 #咖啡廳 #義大利 #台南咖啡廳 #巷弄美食 #台南食記 #成大美食 #下午茶 #tainanfood #tainan #popdaily #popyummy #yummyday #bpintaiwan #vscocam #vscotaiwan #girlstalk #viewtaiwan #igtaiwan #foodie #手機食先 #手機攝影 #vscofoo

In [1515]:
#====== cal one store rating ======

#====== import senti word from antusd ======
word_senti_score = dict(zip(antusd['Word'],antusd['Score'])) # find score via word, 27221 senti words

#====== add senti word from extended dict ======
self_extend_senti_dict(word_senti_score)
self_extend_senti_dict_hotpot(word_senti_score)
add_emoji_senti_score(word_senti_score, emoji_sentiment_dict)
# new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_neg_word_senti') # only add neg word
# add both pos & neg word 
new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_pos_word_senti')
new_antusd_word_senti_dict.update(read_new_antusd_senti('new_antusd_neg_word_senti'))
add_new_antusd_senti_score(word_senti_score, new_antusd_word_senti_dict) 


#====== update senti_dict & jieba_dict ======
emoji_sentiment_dict = read_emoji_csv() # todo: update emoji
self_extend_senti_dict(word_senti_score) 
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict



#====== get articles, followers ======
# fileName = 'pasta/article_JAI 宅' # 
# fileName = 'pasta/article_KAFFE at HOME' # 150
# fileName = 'pasta/article_MINT Pasta 義大利麵' #
# fileName = 'pasta/article_螺絲瑪莉義麵坊' # 168
# fileName = 'pasta/article_村口微光' # 180

fileName = 'beef_noodle/article_永康牛肉麵'




articles = pd.read_csv(open('dataset/ig_article/store_article/'+fileName+'.csv')) 

# remove '\n', delete non-string
all_comments, assigned_index, fans_count, likes = data_preprocess(articles)  

# get each comment's score
all_comments_scores = get_each_comment_score(all_comments,True)
before_norm_comment_score = all_comments_scores[:]
# print('Before norm:\n'+str(all_comments_scores))

#====== normalized all comment's senti_score ======
# all_comments_scores = norm_score_1(all_comments_scores)
# all_comments_scores = norm_score_2(all_comments_scores)
all_comments_scores = max_min_normalization(all_comments_scores)
# print('\nAfter norm:\n'+str(all_comments_scores))


#====== normalized likes ======
befor_norm_likes = likes[:]
likes = [1 if np.isnan(i) else i for i in likes]
likes = max_min_normalization(likes)
# print('likes:\n'+str(likes))



# get store rating
# print('\nstore final score:',get_store_score(fans_count, all_comments_scores, assigned_index)) # weight: fans
store_rating = get_store_score(likes, all_comments_scores, assigned_index)
print('\nstore final score:',store_rating) # weight: likes
print('post count:',len(all_comments_scores))






[0]comment: 排20分鐘都值嘅
sent_score: 0

[1]comment: เนื้อนุ่มละลายในปาก ควรค่าแก่การยืนตากแดดรอเกือบ 20นาที ถ้ากลับไทยแล้วมีคนถามทำไมตัวดำ บอกเลยรอคิวเตี๋ยวเนื้อ #MISSIONCOMPLETE #ข้ามาเพื่อสิ่งนี้
sent_score: 0

[2]comment: 不懂好吃不好吃？一起去排隊 ................，30分鐘後的結論: 如果...東甲的牛肉湯頭+這裡的牛肉=PERFECT🧐😂
不 -0.05
好吃 0.37684395
不 -0.05
好吃 0.37684395
排隊 -0.1
😂 0.221
sent_score: 0.7746879

[3]comment: 台湾旅行雑録③，晩ごはんは、牛肉麺と夜市の胡椒餅。とにかく食べてばかりの私たち（苦笑），・，#牛肉麺 #永康牛肉麺 #胡椒餅美味しい #福州世祖胡椒餅 #台湾グルメ #台湾女子旅 #台湾好き
苦笑 -0.1389825
美味 0.6096725000000001
女子 0.0
sent_score: 0.47069000000000005

[4]comment: #집에간다 #집에갈래😭
😭 -0.09300000000000001
sent_score: -0.09300000000000001

[5]comment: ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，台湾:台北市，「永康牛肉麺」ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，●牛肉麺(ピリ辛しょうゆ味) ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，●四川風ワンタンのラー油あえㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，台湾の老舗牛肉麺のお店，，ピリ辛な醤油ベースのス

In [1516]:
print('\nstore final score:',store_rating) # weight: likes


store final score: 0.14363439361524688


In [1517]:
for before_score,after_score in zip(before_norm_comment_score,all_comments_scores):
    print(str(before_score)+' => '+ str(after_score))
print('\n')


0 => 0.0536094247345085
0 => 0.0536094247345085
0.7746879 => 0.13367963542689504
0.47069000000000005 => 0.10225901313107365
-0.09300000000000001 => 0.0439971284867009
2.1810175000000003 => 0.2790350842146452
-0.325 => 0.020018066879266893
0.649 => 0.12068878242082175
1.6487627999999996 => 0.22402229006746277
0 => 0.0536094247345085
0 => 0.0536094247345085
0.25 => 0.07944893077700205
0 => 0.0536094247345085
2.9272221330000003 => 0.3561613207080059
1.494 => 0.20802631284444995
3.6316725000000005 => 0.4289719187669391
0.34041855 => 0.08879441345331607
0.0676179 => 0.0605982772770314
0 => 0.0536094247345085
0.48200000000000004 => 0.10342799238443605
2.25998735 => 0.2871972518796444
0.66 => 0.12182572068669148
0.139 => 0.06797619009413491
0 => 0.0536094247345085
0.7096725 => 0.1269597721422745
0 => 0.0536094247345085
1.3990398 => 0.19821141419766433
0 => 0.0536094247345085
0 => 0.0536094247345085
2.6276725 => 0.325200462500285
0.5402710000000001 => 0.10945076781084463
3.0829999999999997 => 

In [1518]:
temp_index = 0
for before,after in zip(befor_norm_likes,likes):
    print('['+str(temp_index)+']'+str(before)+' => '+ str(after))
    temp_index += 1
print('\n')

[0]12.0 => 0.0031627372052903968
[1]nan => 0.0
[2]6.0 => 0.001437607820586544
[3]18.0 => 0.00488786658999425
[4]12.0 => 0.0031627372052903968
[5]269.0 => 0.07705577918343876
[6]20.0 => 0.005462909718228867
[7]87.0 => 0.024726854514088556
[8]26.0 => 0.00718803910293272
[9]4.0 => 0.0008625646923519264
[10]11.0 => 0.002875215641173088
[11]2.0 => 0.0002875215641173088
[12]14.0 => 0.0037377803335250145
[13]7.0 => 0.0017251293847038527
[14]21.0 => 0.005750431282346176
[15]66.0 => 0.01868890166762507
[16]11.0 => 0.002875215641173088
[17]25.0 => 0.006900517538815411
[18]32.0 => 0.008913168487636573
[19]7.0 => 0.0017251293847038527
[20]16.0 => 0.004312823461759632
[21]3.0 => 0.0005750431282346176
[22]10.0 => 0.002587694077055779
[23]32.0 => 0.008913168487636573
[24]15.0 => 0.0040253018976423235
[25]39.0 => 0.010925819436457734
[26]36.0 => 0.010063254744105807
[27]63.0 => 0.017826336975273145
[28]17.0 => 0.004600345025876941
[29]2.0 => 0.0002875215641173088
[30]78.0 => 0.022139160437032776
[31]1

In [766]:
# word_senti_score['⠀ ']

# Cal one food kind rating

In [1341]:
# ['pasta','beef_noodle','pork_rice','curry','hongkong']
all_food_kinds = ['beef_noodle']

#====== import senti word from antusd ======
word_senti_score = dict(zip(antusd['Word'],antusd['Score'])) # find score via word, 27221 senti words

#====== add senti word from extended dict ======
self_extend_senti_dict(word_senti_score)
self_extend_senti_dict_hotpot(word_senti_score)
add_emoji_senti_score(word_senti_score, emoji_sentiment_dict)
# new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_neg_word_senti') # only add neg word
# add both pos & neg word 
new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_pos_word_senti')
new_antusd_word_senti_dict.update(read_new_antusd_senti('new_antusd_neg_word_senti'))
add_new_antusd_senti_score(word_senti_score, new_antusd_word_senti_dict) 



#====== update senti_dict & jieba_dict ======
emoji_sentiment_dict = read_emoji_csv() # todo: update emoji
self_extend_senti_dict(word_senti_score) 
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict

#====== select food kind to get store names ======
for select_food_kind in all_food_kinds:
    store_names = get_store_names(select_food_kind)
    
    rank_dict = read_other_rank(all_food_kinds)
    
    # cal_all_store_rating
    all_store_rating, all_store_post_count = cal_all_store_rating(store_names, True) # data_preprocess: pick at most post
    # evaluation
    get_evaluation_result(select_food_kind, rank_dict, all_store_rating, store_names, all_store_post_count)


-----------------Store Name--------------------
富宏牛肉麵

[0]comment: BEST BEEF NOODLE SOUP OF TAIWAN, WALKING DISTANCE OF TAIPEI MAIN STATION. YOU CAN CHOOSE BETWEEN SMALL AND MEDIUM BUT I RECOMMEND MEDIUM ANYWAYS! EVERYTHING IS SO TASTY 😍 DON'T RATE THE BAR FOR ITS LOOKING, JUST GIVE IT A TRY :) (NON ADVERTISEMENT LOL) @FUHONGBEEFNOODLES #BEEF #NOODLES #SOUP #BEEFNOUDLESOUP #BESTSOUP #FOODIE #TRAVELFORFOOD #DIEFORFOOD #BESTSOUPINTAIPEI #TASTYASFUCK #TASTYASFUCK🍁🍁🍁🔥🔥🔥👌👌👌💯💯💯
😍 0.6779999999999999
🍁 0.48200000000000004
🍁 0.48200000000000004
🍁 0.48200000000000004
🔥 0.139
🔥 0.139
🔥 0.139
👌 0.563
👌 0.563
👌 0.563
💯 0.12
💯 0.12
💯 0.12
sent_score: 4.59

[1]comment: .，夜寒くて暖かいもの食べたかったので、，宿近くの富宏牛肉麺へ🐮，このお店24時間営業なんです🥺，(夜遅くに台北着いたらめっちゃ助かる✨)，.，店に着くと席にご案内→注文→注文したものが，届いたらお金を支払うシステムです。，注文してから30秒以内で牛肉麺来ました💦，.，・牛肉麵(大)：$110元，.，テーブルには牛油と酸菜があるので、，適当に入れて食べました😋，麺がモチモチしててすごく美味しい‼️，牛肉もしっかり味がついてます🐮，八角入ってなさそうなので、，苦手な人でも食べられると思います👌，ちなみにドリンクは入口付近にある冷蔵庫から，1本勝手に持っていっていいらしいです🥤，ここの牛肉麺はオススメです👍，.，#富宏牛肉麵 #富宏牛肉麺 #北門 #西門町 #牛肉麺 #


[0]comment: 排20分鐘都值嘅
sent_score: 0

[1]comment: เนื้อนุ่มละลายในปาก ควรค่าแก่การยืนตากแดดรอเกือบ 20นาที ถ้ากลับไทยแล้วมีคนถามทำไมตัวดำ บอกเลยรอคิวเตี๋ยวเนื้อ #MISSIONCOMPLETE #ข้ามาเพื่อสิ่งนี้
sent_score: 0

[2]comment: 不懂好吃不好吃？一起去排隊 ................，30分鐘後的結論: 如果...東甲的牛肉湯頭+這裡的牛肉=PERFECT🧐😂
不 -0.05
好吃 0.37684395
不 -0.05
好吃 0.37684395
排隊 -0.1
😂 0.221
sent_score: 0.7746879

[3]comment: 台湾旅行雑録③，晩ごはんは、牛肉麺と夜市の胡椒餅。とにかく食べてばかりの私たち（苦笑），・，#牛肉麺 #永康牛肉麺 #胡椒餅美味しい #福州世祖胡椒餅 #台湾グルメ #台湾女子旅 #台湾好き
苦笑 -0.1389825
美味 0.6096725000000001
女子 0.0
sent_score: 0.47069000000000005

[4]comment: #집에간다 #집에갈래😭
😭 -0.09300000000000001
sent_score: -0.09300000000000001

[5]comment: ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，台湾:台北市，「永康牛肉麺」ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，●牛肉麺(ピリ辛しょうゆ味) ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，●四川風ワンタンのラー油あえㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，ㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤㅤ，台湾の老舗牛肉麺のお店，，ピリ辛な醤油ベースのス

抉擇 0.0
挑選 0.20398139999999998
上來 0.05543455
旅客 0.0
可能 0.0
舒適 0.45
享用 0.0
美食 0.16
XD 0.1
夠味 0.0
不 -0.05
死鹹 -0.2
好吃 0.37684395
入口即化 0.3
類似 0.0
非常 0.0788721
特色 0.18265335
味道 0.0
沒什麼 -0.3
不 -0.05
其實 0.2
拉麵 0.15
一樣 0.0540008
人山人海 0.0280856
撐 0.2
排隊 -0.1
專心 0.46404855
沒什麼 -0.3
時間 0.0550611
口渴 -0.1116528
😅 0.17800000000000002
下次 0.1
可以 0.1551797
換成 0.3608607
棒 0.13
沒有 -0.0921865
非常 0.0788721
足夠 0.31770235
全部 0.21227100000000002
好吃 0.37684395
包含 0.0289814
特色 0.18265335
只差 -0.01
麵條 0.0
而已 -0.0289814
機會 0.3837311
可以 0.1551797
嘗試 0.05
太快 0.20763225
不到 -0.4717674
👍 0.25
美食 0.16
推薦 0.019754
推薦 0.019754
sent_score: 5.659217099999999

[16]comment: 여긴 완전 추천 진한 갈비탕 맛 고기도 엄청 많이 들어있고 부드럽다 국물 완전 얼큰 캬😆 #유산동우육면 #대만맛집 #우육면맛집 #劉山東牛肉麵 #TAIPEIFOOD #대만여행 #BERRY_대만，.，.，💰우육면 NT$150
😆 0.409
💰 0.251
sent_score: 0.6599999999999999

[17]comment: 我親愛的小天使老爸
親愛 0.7535361999999999
小天使 0.0626976
老爸 0.0
sent_score: 0.8162337999999999

[18]comment: TAIWAN BEEF NOODLES #BEEFNOODLES #劉山東牛肉麵 #FOODPORN #FOODIE #FOODSTAGRAM #FOOD

美味 0.6096725000000001
🍥 0.05
美味 0.6096725000000001
大好 0.43823609999999996
新鮮 0.28997490000000004
♪ 0.534
女子 0.0
sent_score: 2.531556

[45]comment: BACK HERE AGAIN FOR THE BEEF NOODLE SOUP. THIS IS ONE OF MY LATE NIGHT GO-TOS👌🏼 THEY RENOVATED THE WHOLE PLACE AND NOW IT LOOKS ALL MODERN AND NICE. BUT I MISSED THE OLD STORE THEY HAD🥺，—- .，.，.，.，#TASTETHISNEXT#TAIPEIFOODIE#TAIPEI#BEEFNOODLES#YELPELITE#FOODADVENTURE#TAIPEIEATS#TODAYFOOD#牛肉麵#台北美食#BESTFOODFEED#TAIWANFOOD#EATMUNCHIES#TAIPEIFOOD
👌 0.563
美食 0.16
sent_score: 0.723

[46]comment: 。，元氣大傷，補一下
元氣大傷 -0.19345725
sent_score: -0.19345725

[47]comment: 必比登推薦 林東芳牛肉麵，，#牛肉麵 #半筋半肉牛肉麵
推薦 0.019754
sent_score: 0.019754

[48]comment: REALLY TASTE GOOD
sent_score: 0

[49]comment: #우육면 ><
sent_score: 0

[50]comment: 林東芳牛肉麵，對牛肉麵辨別度很低，桌上的牛油沒有建宏好吃就是，牛肉麵 $170（小），#林東芳 #牛肉麵 #台北牛肉麵 #BEEFNOODLES #TAIPEIFOOD #TAIPEIBEEFNOODLES #台北グルメ #台北牛肉麺 #台北美食 #林東芳牛肉麵
辨別 0.0
沒有 -0.0921865
好吃 0.37684395
美食 0.16
sent_score: 0.44465745

[51]comment: 牛肉還是很好吃😋！#林東芳牛肉麵 #八德路二段#牛


[63]comment: 台南第一餐吃牛肉麵🐂🍜，#台南美食 #黑旋風乖乖牛肉麵 #紅燒牛肉麵 #台南
🐂 0.14300000000000002
🍜 0.15
美食 0.16
sent_score: 0.45300000000000007

[64]comment: 108.04.17，北門路上的牛肉麵，吃完真的很爽！！，#好吃好喝
很爽 0.175
sent_score: 0.175

[65]comment: 先前幫同事買過兩次蕃茄牛肉麵，每次內用都爆滿...今天總算吃到了！!湯頭清爽甜味明顯，肉的部份推測是半筋半肉混牛筋，筋的部份口感Q彈，瘦肉就部份不柴但也沒特別香算中規中矩;雖然是外帶，麵條嚐起來嚼勁還是有嚼勁，肉量也算有誠意，並且菜單上每種口味根據個人食力不同有四種份量可供消費者選擇，個人覺得這種設計還蠻貼心的~...GOOGLEMAPS小魯給五顆星！~@^_^@~
爆滿 0.0644288
明顯 0.46633009999999997
推測 0.030246
沒 -0.1
特別 0.31378590000000006
中規中矩 -0.05
麵條 0.0
還是 0.1
誠意 0.5694408000000001
根據 0.02722505
不同 0.0
選擇 0.0210186
覺得 0.02
設計 -0.0134571
sent_score: 1.4490181499999997

[66]comment: /，乖乖牛肉麵，放入再訪名單
sent_score: 0

[67]comment: 跑友推薦吃起來
推薦 0.019754
sent_score: 0.019754

[68]comment: *，總店有和牛🤤，這一碗叫搞死自己炙燒和牛燒肉麵，500元，吃完很滿足❤️，-，-，#CHIIBLOG2019，#CHIIBLOG201910，#台南 #台南美食 #台南牛肉麵 #台灣牛肉麵 #牛肉麵 #黑炫風乖乖牛肉麵 #和牛
🤤 0.15
自己 0.0
滿足 0.57707005
❤ 0.746
美食 0.16
sent_score: 1.63307005

[69]comment: 🌳，其實我一直覺得菜單設計這一塊可以不用那麼呆板乏味，這樣生動活潑不也讓生活增添許多樂趣不是嗎😆，#乖乖愛吃花椰菜🥦，#寵物友善，#彩虹友善
🌳 0.486
其實 0.

好吃 0.37684395
便宜 0.0
還有 0.2078135
豆漿 0.0
免費 0.0264712
依然 0.08355510000000001
還能 0.25
喜好 0.8426861999999999
😋 0.25
足夠 0.31770235
👭 0.46299999999999997
忍不住 0.4150174
軟嫩 0.1
不 -0.05
麵條 0.0
自取 0.0
軟嫩 0.1
入味 0.0
十足 0.31264125
✏ 0.342
人潮 0.0
眾多 0.0
沒有 -0.0921865
車位 0.0
建議 0.0
可以 0.1551797
🐠 0.414
👀 0.063
🐵 0.478
🐵 0.478
🐵 0.478
🐵 0.478
🙈 0.43200000000000005
🐠 0.414
👀 0.063
🐠 0.414
👀 0.063
美食 0.16
豆漿 0.0
🚚 -0.077
☎ 0.0
⏰ 0.0
🐠 0.414
👀 0.063
真心 0.6929350000000001
分享 0.06795875
歡迎 0.475
分享 0.06795875
不能 -0.060934800000000004
錯過 -0.5726038
美食 0.16
sent_score: 9.26603805

[23]comment: 急強降雨中03級休四乙校友來訪，記得以前這種天氣妳們不是翹課（自動放假），就是遲到啦😭😭！，感謝曾盈瑄大美女的日出鳳梨酥，妳的壞嘴💋師承於我，真的被我教壞😄😄，出了社會這一年的歷練夠成熟有懂事了耶！，國軍ONLINEAARON WANG在校的時候，跟你說十句話我有九句是在碎念你！今天看到你被國家栽培照顧，言談舉止真的有改變，會替自己想也會替別人想了！，呵！呵！真的是不需要再唸你了啦！，開心聽到你說自己會賺錢💰了，謝謝你的老皮買單啦！，兩位加油囉！，，愛嘮叨的楊爸，1080611
記得 0.2896336
不是 -0.7609348000000001
翹課 0.0
自動 0.07101360000000001
遲到 -0.15541629999999998
😭 -0.09300000000000001
😭 -0.09300000000000001
感謝 0.4296968
日出 0.0
💋 0.691
😄 0.421000000

加點 0.1
sent_score: -0.5596536

[75]comment: 黃金泡菜好吃！，，#牛肉厲害
黃金 0.0830536
好吃 0.37684395
厲害 0.2
sent_score: 0.6598975499999999

[76]comment: 吃麵記得買酒
記得 0.2896336
sent_score: 0.2896336

[77]comment: 雪花豬肉麵
sent_score: 0

[78]comment: 天氣好冷，好適合來一碗熱熱的湯，#牛肉麵 #美福
適合 0.775
sent_score: 0.775

[79]comment: 熟成牛腩 $180 VS 椒香金牌 ＄285，，#牛肉麵 ，#內湖美食
美食 0.16
sent_score: 0.16

[80]comment: 牛肉品質好的，湯頭簡單清爽，及格的牛肉麵，#牛肉麵 #BEEFNOODLES
簡單 0.026052
及格 0.10533889999999999
sent_score: 0.13139089999999998

[81]comment: 加顆蛋就是牛雪花
sent_score: 0

[82]comment: 招待卷送的牛肉麵加減吃，小菜牛筋和泡菜完全搶過牛肉麵本身的風采🤣，牛筋好吃!，#滷牛筋#紅燒牛肉麵#愛熟成21牛肉麵 #美福
招待 0.1350369
送 0.15
完全 0.45943999999999996
風采 0.1112152
好吃 0.37684395
sent_score: 1.23253605

[83]comment: 豬膝麵✌
✌ 0.46299999999999997
sent_score: 0.46299999999999997

[84]comment: 今天上班唯一的動力， #廢物二姐的🐷食光
唯一 0.0540008
動力 0.1697184
廢物 -0.43000900000000003
🐷 0.368
sent_score: 0.16171019999999997

[85]comment: 湯頭非常的清甜，採用美國牛及澳洲牛筋🍜，-，#熟成牛 #美福 #牛肉麵 #美國牛 #澳洲牛肉 #清燉牛肉麵 #內湖 #BEEFNOODLESOUP #NEIHU #TAIPIE #LOVETOEAT #YUMMY

推薦 0.019754
適合 0.775
使用 0.24782015
黃金 0.0830536
強調 0.0983498
即使 0.0
保有 0.4004119
味道 0.0
非常 0.0788721
🍤 0.053
還有 0.2078135
南瓜 0.0
用心 0.51575515
細心 0.565104
強調 0.0983498
保有 0.4004119
味道 0.0
薄薄的 -0.02
直接 0.326906
必點 0.1
👯 0.439
乾淨 0.0
😝 0.423
覺得 0.02
非常 0.0788721
值得 0.23
讚賞 0.45
通常 0.22094120000000003
味精 -0.1
油膩 -0.0289814
口渴 -0.1116528
非常 0.0788721
推薦 0.019754
✅ 0.40700000000000003
推薦 0.019754
興趣 0.6196368
前往 0.0710186
一定 0.2731792
電話 0.0
美食 0.16
美食 0.16
好吃 0.37684395
美食 0.16
推薦 0.019754
高CP值 0.2
sent_score: 23.208992608000006

[53]comment: 感謝🙏 CARTER CHEN 書法大師賞賜！！，讓樂客添增幾分過年喜氣，讚👍👍！ 📍樂客牛肉麵 ROCK’S BEEF NOODLES，🏡 新竹市區西大路247號，☎ 訂購專線：0928-659955，(店內位置有限，僅接受現場候位) 🅿️ 開車的朋友建議可以停在‘樂民’或‘明志書院’停車場（走路皆4分內到喲），，#台灣美食 #新竹美食 #老宅 #牛肉麵 #老宅餐廳 #樂客 #好吃 #牛肉面 #職人 #舊窗 #新竹火車站，#OLDHOUSE #HSINCHU #BEEFNOODLES #LIFESTYLE #FOOD #HSINCHURESTAURANT #HINCHUFOOD #DELICIOUS #YUMMY
感謝 0.4296968
🙏 0.41700000000000004
大師 0.045549900000000004
喜氣 0.4675356
讚 0.25
👍 0.25
👍 0.25
📍 0.111
🏡 0.436
☎ 0.0
訂購 0.05
有限 -0.0828135
接受 0.0

😂 0.221
😬 0.19399999999999998
😘 0.701
憐憫 0.15543455
憐憫 0.15543455
滿滿 0.5288576
sent_score: 1.9557267

[64]comment: 點了滿桌沒有一塊牛肉😂，他們的招牌是小菜，牛肉麵不行
沒有 -0.0921865
😂 0.221
不行 -0.3465882
sent_score: -0.21777470000000002

[65]comment: ：，🔺紅燒牛肉麵💰130(大)，🔺清燉牛肉麵💰165(小)，🔺小菜💰40/盤，大概說到左營牛肉麵我的想法就是這家三牛～犇～大小碗差10塊錢❗️聰明人可能會是點一碗大的一起SHARE再點些別的⋯可見我不是聰明人🤣小菜有很多選擇但一盤40塊可能可以斟酌一下，清燉紅燒各有所好，口味很是大眾接受，連不是用餐時間還是不少人(包含外國觀光客)肉是HEN大塊也不錯吃(膠質可以推推)不過紅燒的肉比較像是肉乾的口味跟口感，清燉的肉我比較喜歡～😍喔麵條部分我們都是選拉麵，也有別種麵條可以選擇，菜單在最後可參考🤤歡迎分享你覺得好吃的牛肉麵我再去吃看看✌🏻，🚩高雄市左營區勝利路85號，#EAT #EATING #EATINGLIFE #KAOHSIUNG #KAOHSIUNGFOOD #BEEFNOODLES #TAIWAN #BEEF #FOODIE #高雄美食 #高雄左營 #左營美食 #粒粒吃貨IN高雄 #不專業的吃貨 #粒粒吃左營 #左營牛肉麵 #三牛牛肉麵 #犇 #左營區美食 #蓮池潭美食 #高雄 #左營
💰 0.251
💰 0.251
💰 0.251
差 -0.2
❗ 0.1
可能 0.0
可見 0.32905305
不是 -0.7609348000000001
很多 0.28742399999999996
選擇 0.0210186
可能 0.0
可以 0.1551797
接受 0.0
不是 -0.7609348000000001
時間 0.0550611
還是 0.1
不少 0.47488919999999996
包含 0.0289814
不錯 0.2
可以 0.1551797
推推 0.3
不過 0.0
喜歡 0.875
😍 0.6779999999999999
麵條 0.0
拉麵 0.15
麵條 0.0
可以 0.1551797
選

# Cal all food kind rating

In [1429]:
#====== MSE ======
# input store name: [a,b,c]
# output: [score.....]
def cal_all_store_rating(store_names, print_comment):
    if print_comment:
    
        all_store_rating = []
        all_store_post_count = [] # store info dict.
        for i,name in enumerate(store_names[1:]):
            print('-----------------Store Name--------------------')
            print(name)
            fileName = '/article_' + name
            articles = pd.read_csv(open('dataset/ig_article/store_article/'+store_names[0]+fileName+'.csv')) 

            # remove '\n', delete non-string
            all_comments, assigned_index, fans_count, likes = data_preprocess(articles)  

            # get each comment's score
            all_comments_scores = get_each_comment_score(all_comments,print_comment)

            # normalize senti score
    #         all_comments_scores = norm_score_1(all_comments_scores)
    #         all_comments_scores = norm_score_2(all_comments_scores)
            all_comments_scores = max_min_normalization(all_comments_scores)

            # normalized likes
            likes = [1 if np.isnan(i) else i for i in likes]
#             likes = norm_score_1(likes)
#             likes = norm_score_2(likes)
            likes = max_min_normalization(likes)

            # get store rating
            # print('\nstore final score:',get_store_score(fans_count, all_comments_scores, assigned_index)) # weight: fans
            store_rating = get_store_score(likes, all_comments_scores, assigned_index)

            print('\nstore final score:',store_rating) # weight: likes
            all_store_rating.append(store_rating)
            all_store_post_count.append(len(all_comments))
    
    else:
        all_store_rating = []
        all_store_post_count = [] # store info dict.
        for i,name in enumerate(store_names[1:]):

            fileName = '/article_' + name
            articles = pd.read_csv(open('dataset/ig_article/store_article/'+store_names[0]+fileName+'.csv')) 

            # remove '\n', delete non-string
            all_comments, assigned_index, fans_count, likes = data_preprocess(articles)  

            # get each comment's score
            all_comments_scores = get_each_comment_score(all_comments,print_comment)

            #====== normalize senti score ======
#             all_comments_scores = norm_score_1(all_comments_scores)
#             all_comments_scores = norm_score_2(all_comments_scores)
            all_comments_scores = max_min_normalization(all_comments_scores) # best

            #====== normalized likes ======
            likes = [1 if np.isnan(i) else i for i in likes]
#             likes = norm_score_1(likes)
#             likes = norm_score_2(likes)
            likes = max_min_normalization(likes)


            # get store rating
            # print('\nstore final score:',get_store_score(fans_count, all_comments_scores, assigned_index)) # weight: fans
            store_rating = get_store_score(likes, all_comments_scores, assigned_index)

    #         print('\nstore final score:',store_rating) # weight: likes
            all_store_rating.append(store_rating)
            all_store_post_count.append(len(all_comments))
        
        
    return all_store_rating,all_store_post_count

In [1513]:
#===================================== main function =======================================
all_food_kinds = ['pasta','beef_noodle','pork_rice','curry','hongkong']


#====== import senti word from antusd ======
word_senti_score = dict(zip(antusd['Word'],antusd['Score'])) # find score via word, 27221 senti words

#====== add senti word from extended dict ======
self_extend_senti_dict(word_senti_score)
self_extend_senti_dict_hotpot(word_senti_score)
add_emoji_senti_score(word_senti_score, emoji_sentiment_dict)
# new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_neg_word_senti') # only add neg word
# add both pos & neg word 
new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_pos_word_senti')
new_antusd_word_senti_dict.update(read_new_antusd_senti('new_antusd_neg_word_senti'))
add_new_antusd_senti_score(word_senti_score, new_antusd_word_senti_dict) 



#====== update senti_dict & jieba_dict ======
emoji_sentiment_dict = read_emoji_csv() # todo: update emoji
self_extend_senti_dict(word_senti_score) 
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict


#====== select food kind to get store names ======
mse_record = {}

for select_food_kind in all_food_kinds:
    store_names = get_store_names(select_food_kind)

    
    rank_dict = read_other_rank(all_food_kinds)
#     print(rank_dict)
    
    # cal_all_store_rating
    all_store_rating, all_store_post_count = cal_all_store_rating(store_names,False) # data_preprocess: pick at most post
    # evaluation matrix
    new_mse = get_evaluation_result(select_food_kind, rank_dict, all_store_rating, store_names, all_store_post_count)
    mse_record[select_food_kind] = new_mse

print('\nMse:'+str(mse_record))


===================== pasta rank =====================
第1名: JAI 宅 0.35864 , 150 post , 1
第2名: MINT Pasta 義大利麵 0.33187 , 109 post , 2
第3名: HUN 混 0.28592 , 150 post , 4
第4名: La PASTA 義大利麵屋 0.23008 , 103 post , 7
第5名: MIGA KITCHEN PASTA_米家廚房 0.16349 , 87 post , 9
第6名: Dor留 手工義大利麵 - 友愛街店 0.24593 , 85 post , 6
第7名: petit doux．微兜 Café Bistro 0.12931 , 147 post , 10
第8名: KAFFE at HOME 0.32231 , 150 post , 3
第9名: 螺絲瑪莉義麵坊 0.17984 , 150 post , 8
第10名: 村口微光 0.27547 , 150 post , 5

新評分機制排名: [1, 2, 4, 7, 9, 6, 10, 3, 8, 5]
MSE: 8.6
r2_score: -0.042
--------------------Google--------------------
Google_rank: [1, 2, 2, 10, 2, 8, 6, 9, 7, 2]
Google_MSE: 12.0
Google_r2_score: -0.455
--------------------ifoodie--------------------
ifoodie_rank: [3, 4, 5, 10, 1, 8, 2, 9, 6, 6]
ifoodie_MSE: 11.9
ifoodie_r2_score: -0.442

===================== beef_noodle rank =====================
第1名: 富宏牛肉麵 0.32829 , 147 post , 1
第2名: 永康牛肉麵 0.14363 , 150 post , 9
第3名: 劉家山東牛肉麵 0.29695 , 150 post , 3
第4名: 林東芳 0.32629 , 15

In [1514]:
print('Mse:'+str(mse_record))
print('Senti words count:'+str(len(word_senti_score)))

Mse:{'pasta': 8.6, 'beef_noodle': 8.6, 'pork_rice': 13.8, 'curry': 14.0, 'hongkong': 13.4}
Senti words count:28525


In [43]:
mae(np.array(range(1,11)),np.array([9,2,5,4,3,7,1,8,6,10]))

# output ramen rating 
# output_csv('ramen_rating.csv', [[fileName, store_rating]], 'a+')

2.2

In [1397]:
'''only for check word segment's senti score'''


#===================================== main function =======================================
all_food_kinds = ['pasta','beef_noodle','pork_rice','curry','hongkong']


#====== import senti word from antusd ======
word_senti_score = dict(zip(antusd['Word'],antusd['Score'])) # find score via word, 27221 senti words

#====== add senti word from extended dict ======
self_extend_senti_dict(word_senti_score)
self_extend_senti_dict_hotpot(word_senti_score)
add_emoji_senti_score(word_senti_score, emoji_sentiment_dict)
# new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_neg_word_senti') # only add neg word
# add both pos & neg word 
new_antusd_word_senti_dict = read_new_antusd_senti('new_antusd_pos_word_senti')
new_antusd_word_senti_dict.update(read_new_antusd_senti('new_antusd_neg_word_senti'))
add_new_antusd_senti_score(word_senti_score, new_antusd_word_senti_dict) 



#====== update senti_dict & jieba_dict ======
emoji_sentiment_dict = read_emoji_csv() # todo: update emoji
self_extend_senti_dict(word_senti_score) 
jieba.load_userdict('dataset/dic_trad/self_define_dict.txt') # load self-define dict


#====== select food kind to get store names ======
mse_record = {}

for select_food_kind in all_food_kinds:
    store_names = get_store_names(select_food_kind)

    
    rank_dict = read_other_rank(all_food_kinds)
#     print(rank_dict)
    
    # cal_all_store_rating
    all_store_rating, all_store_post_count = cal_all_store_rating(store_names,True) # data_preprocess: pick at most post
    # evaluation matrix
    new_mse = get_evaluation_result(select_food_kind, rank_dict, all_store_rating, store_names, all_store_post_count)
    mse_record[select_food_kind] = new_mse

print('\nMse:'+str(mse_record))

-----------------Store Name--------------------
JAI 宅

[0]comment: 意外找到一間網美餐廳，來到這人人都是網美💛，網美聖地💓，每個角落都很好拍 餐點也好吃，玩到被店員提醒餐點涼掉就不好吃囉🥴，，#台中美食#TAICHUNG#JAI宅#吃貨動起來#食在好好吃#非吃不可#美好食光# 潔妮 日常#台中景點#網美景點
意外找到 0.3
網美 0.1
網美 0.1
💛 0.7090000000000001
網美 0.1
聖地 0.2
💓 0.664
很好拍 1.0
好吃 0.37684395
提醒 0.013909999999999999
不 -0.05
好吃 0.37684395
美食 0.16
食在好好吃 0.8
非吃不可 0.8
美好食光 0.8
景點 0.0
網美 0.1
景點 0.0
sent_score: 6.5505979

[1]comment: 第一次來是粉色頭髮，第二次來還是粉色😂，他們的青醬爆炸蛤蜊義大利麵真的推👈，#網美當起來😎
第一次 0.036000533
還是 0.1
😂 0.221
爆炸 0.0
真的推 0.8
👈 0.424
網美 0.1
😎 0.1
sent_score: 1.7810005330000003

[2]comment: 190823 🥳
🥳 0.8
sent_score: 0.8

[3]comment: 認真傾聽自己內在的聲音❤️
認真 0.5221302
傾聽 0.0
自己 0.0
❤ 0.746
sent_score: 1.2681301999999999

[4]comment: -，0907，•橘醬爆炸蛤蜊義大利麵，•明太子炭烤雞肉串，•黑松露爆炸蛤蜊飯（加焗烤），•JAI現炸脆薯，-，義大利麵超級好吃，那個醬太猛了 吃完還會想再點一份，蛤蜊也真的爆炸多的，雞肉串是店員推薦的，很令人驚艷的雞肉串，咬下去 裡面超級超級嫩，又有滿滿的肉汁 加上外面的明太子 太好吃了，燉飯跟薯條 我就覺得普通了，來這裡點義大利麵就對了，-，而且他號稱台中最美的餐廳，裡面空間很大 各個地方都有精心佈置 絕對是會回訪的店❤️
爆炸 0.0
爆炸 0.0
超級 0.0676179
好吃 0.37684395
還會想再點一份 5.0
爆炸 0.0
推薦 0.019754
驚艷 0.

😌 0.48200000000000004
sent_score: 2.3438326

[101]comment: （補2019.07.31），最近是「美美」代言的宅，裡面佈置很網美風格，很適合拍照📷，餐點也很美味，我覺得也很適合家庭聚餐😋，#台中美食 #義大利麵 #義大利燉飯 #披薩🍕 #鬆餅 #美美 #ピザ🍕 #スパゲッティ🍝 #台中 #たいちゅう
代言 0.0
網美 0.1
適合 0.775
📷 0.43
美味 0.6096725000000001
覺得 0.02
適合 0.775
聚餐 0.1
😋 0.25
美食 0.16
🍕 0.41700000000000004
🍕 0.41700000000000004
🍝 0.11699999999999999
sent_score: 4.1706725

[102]comment: ➰，收藏好久亡美店果然名不虛傳，一進店門稍覺擁擠，往內走卻有一股豁然天明的感賊～，真的好拍好美又好食🤤，份量也讓我們飽到天邊去，推薦指數五燈獎✨✨✨✨✨
➰ -0.091
收藏 0.20756149999999998
好久 -0.05
果然 0.1125365
名不虛傳 0.3
擁擠 -0.2184721
豁然 0.0
天明 0.0
🤤 0.15
推薦 0.019754
五燈獎 3.0
✨ 0.35100000000000003
✨ 0.35100000000000003
✨ 0.35100000000000003
✨ 0.35100000000000003
✨ 0.35100000000000003
sent_score: 5.1853799

[103]comment: 試吃減肥藥第一天🤔️
sent_score: 0

[104]comment: 。，2019.09.17，這趟最最最期待的就是#JAI宅 ，#JAI橘醬爆炸蛤蜊宅宅麵 ，#明太子奶油花椒檸檬雞腿燉飯，哈哈以後有空再PO文好好介紹一番，-，限時動態大家都在問，有滿滿1:1復仇者人偶、模型在哪兒，在#台中 #歐雅英雄主題館 ，裡面幾乎都是絕版非賣品，所以就拍拍照過過乾癮囉哈哈，其實在土城秀泰1F就有一間歐雅囉，只是比較小間一點而已，-，#小小七手工湯包 ，昨天踩空，今天特地再跑一趟，#小蝦仁湯包 ，#大鮮肉湯包 ，阿嗚～滿滿的湯汁摳摳勞，真的是超級好吃的🤤，-，#龍貓

南瓜 0.0
😂 0.221
😂 0.221
覺得 0.02
感動 0.1269683
sent_score: 0.49678180000000005

[78]comment: 大學時期懷念的好味道，真的好好吃～～～
懷念 0.2522301
味道 0.0
好吃 0.37684395
sent_score: 0.62907405

[79]comment: 評價如圖，FYI.
sent_score: 0

[80]comment: 這好像是上學期結業式吧？，監視器真的很幸福🥰
好像 0.44268620000000003
幸福 0.45
🥰 0.25
sent_score: 1.1426862

[81]comment: 餐點平價不錯吃！飲料就普普的
不錯 0.2
sent_score: 0.2

[82]comment: 以這個價位 這個份量 這個價格來說。CP值算高～這無話說👍，，不過好幾年沒來吃了，記得第一次去吃的時候遇到人超級多，排隊也亂七八糟，今天去吃 還是一樣...有人沒排隊就在亂走亂找位子 沒有排隊 看到位子就直接去做 傻眼🙄🙄媽媽帶著小孩這樣 真沒教養 當排隊的人是白癡！，還沒吃到心情就很差...店裡寫著自助找位 三區地板寫著等候排隊區 但插隊的還是直接就給你坐下去 也不會有店裡的人出門管 因為太忙了...完全能理解店員的辛苦..但..YOU KNOW😂 🍝其實這樣 我更推信義也有的 永和也有的店#創義麵，其實也算平價 CP值很高 HEN好吃！環境好，今日食，💰135 茄汁野菇雞肉，💰140 鴨胸麵，💰25 阿薩姆紅茶（蠻大杯），#台北市#景美#MINTPASTA#義大利麵#世新美食#好食#TAIPEIFOOD#TWIG#HIGH#CALORIES#FIGHTING#HAPPY#手機先食#TAIPEI#TAIPEIFOOD#POPYUMMY #DELICIOUS#GOOD#YUMMY#EATS#LOVE#TAIWAN#MISS#FOODPIC#INSTAFO#POPYUMMY#小安美食區
CP值算高 0.2
👍 0.25
不過 0.0
沒來 -0.02
記得 0.2896336
第一次 0.036000533
遇到 0.0445837
超級 0.0676179
排隊 -0.1
亂七八糟 -0.5625
還是 0.1
一樣 0.0540008
沒 -

生日快樂 0.383642475
🎂 0.613
🎉 0.738
sent_score: 3.0455293500000002

[49]comment: 190914，-，高中朋友約見面囉🤪🤪
sent_score: 0

[50]comment: 在台灣也可以吃到荷蘭小鬆餅🥞❤️，📍台中市一中街158號前，還沒吃過的朋友一定要試試，台中人真的好有福氣🥰，-，HUN混（不知道為什麼想要標地點找不到搜尋就有😢），適合好友聚會👍，廁所真的太可愛了，#台中北區 #台中 #台中北區美食 #荷蘭小鬆餅 #有荷不渴 #HUN混 ，#ZAI遊台中👣
可以 0.1551797
❤ 0.746
📍 0.111
沒吃過 -0.03
一定要試試 5.0
🥰 0.25
不 -0.05
知道 0.529169
想要 0.27222515
不到 -0.4717674
搜尋 0.1
😢 0.006999999999999999
適合 0.775
好友 0.1
👍 0.25
可愛 0.6611292
美食 0.16
👣 0.344
sent_score: 8.908935649999998

[51]comment: #20190730 #久違 ，懂得已經失去與未來所獲得，生活就是在，一點一滴經驗與成長中度過，#願 妳我都有更美好的未來，#HUN混 ，#橘醬超級爆炸蛤蜊義大利麵
久違 0.0
懂得 0.4646335999999999
已經 0.029755599999999997
失去 -0.74838315
獲得 0.53745375
經驗 0.0702444
成長 0.6377666999999999
度過 0.1751043
美好 0.8176861999999999
超級 0.0676179
爆炸 0.0
sent_score: 2.0518792999999995

[52]comment: 好像很久沒跟這位小姐見面了，還沒畢業幾乎每個禮拜見，一直在我面前喊邊緣沒朋友😑，@SMLIEGHOSTLY85315 沒關係妳至少還有我（嗯？🥴🥴，是不～～，#HUN混 #炸蝦義大利麵 #邊緣跟邊緣有約 #休假的小確幸 #YYUEAT
好像 0.44268620000000003
小姐 0.0
還沒 -0.4
畢業 0.0
幾乎 0.0315279
禮拜 0.0
一直 0.2729052
邊緣 


store final score: 0.2858895177412654
-----------------Store Name--------------------
La PASTA 義大利麵屋

[0]comment: 是的！我今天很餓⋯ ，#餓著肚子 #好久沒吃義大利麵了
久沒吃 0.25
sent_score: 0.25

[1]comment: 奶油燻雞手工麵
sent_score: 0

[2]comment: 撐死我了
sent_score: 0

[3]comment: 一個人的下午茶
sent_score: 0

[4]comment: 🐙，一個過家門而不入的孝子，一個請假跟朋友吃飯的認真員工，沒辦法，誰叫我們半年沒有好好聚聚聊天了
🐙 0.387
吃飯 0.0
認真 0.5221302
沒 -0.1
沒有 -0.0921865
聚聚 0.0
sent_score: 0.7169437000000001

[5]comment: 運動的理由就在動完吃一波，送啦，#寬麵比較有咬勁 #我好累真的好累身體很軟😂
理由 0.0
送 0.15
身體 0.0
😂 0.221
sent_score: 0.371

[6]comment: 🍝，#辣味番茄雞蓉細麵 #食記 #台北美食 #FLORA_FOODIARY
🍝 0.11699999999999999
美食 0.16
sent_score: 0.277

[7]comment: 聚餐
聚餐 0.1
sent_score: 0.1

[8]comment: 生活可能會遇到很多困惑、迷惘，唯有肚子餓這件事.....無庸置疑！ฅ´•ᴥ•`ฅ🍴，#LAPASTA #PASTA #SPAGHETTI #FOODIE #RINASHOTSHOT #HAPPYKISSANNVERSARY
可能 0.0
遇到 0.0445837
很多 0.28742399999999996
困惑 0.0
迷惘 -0.0795256
唯有 0.0
無庸置疑 0.346479375
🍴 0.537
sent_score: 1.1359614749999998

[9]comment: 阿母的最愛！打卡送冰磚！，，@LAPASTATW
阿母 0.0
最愛 0.5801090999999999
送 0.15
sent_score: 0.730

...

😋 0.25
飲茶 0.0
送 0.15
烙賽 -0.25
sent_score: -0.36353080000000004

[33]comment: 尾牙吃起來
sent_score: 0

[34]comment: 瑤柱雞絲羹、流沙包、燒賣好吃
沙包 0.0
好吃 0.37684395
sent_score: 0.37684395

[35]comment: ♥️🥃🥢 .，#吉星港式飲茶，#台北，#台湾，#台湾グルメ ，#大根餅，#台湾旅行，#旅行，#MEETCOLORSTAIWAN，#GREEN，#OLYMPUSPEN ，#FOODSTAGRAM ，#FOODIE ，#DINNER ，#TAIPEI，#TAIWAN，#TAIWANFOOD ，#TAIWANTRAVEL ，#ABRICOTGOURMET ，#🥢#🥃#♥️
♥ 0.657
飲茶 0.0
♥ 0.657
sent_score: 1.314

[36]comment: 兩個強迫症在新年第三天就約成了！，要一直督促彼此更好才行💗💗💗
強迫症 -0.319578867
一直 0.2729052
督促 0.030246
更好 0.3426862
💗 0.657
💗 0.657
💗 0.657
sent_score: 2.297258533

[37]comment: 騎人節
sent_score: 0

[38]comment: 朝ごはん🤤，吉星港式飲茶のご紹介🤗，台北 中山駅から徒歩10分，台湾のお粥が驚きの美味しさでした😆，エッグタルトは、甘さ控え目。台湾でしか食べられないという卵あんの饅頭は、トロっとしていますがざらついていて・・・食べた事の無い味でした。，24時間営業の現地でも人気のお店だそうです。，お粥が本当におススメです‼️，#台湾旅行 #台湾料理 ，#お粥  #吉星港式飲茶 ，#朝ごはん
🤤 0.15
飲茶 0.0
美味 0.6096725000000001
😆 0.409
時間 0.0550611
現地 0.0
飲茶 0.0
sent_score: 1.2237336

[39]comment: 老公犒賞我的生日餐
生日 0.0
sent_score: 0.0

[40]comment: 宵夜時段~最愛的港式飲茶
宵夜 0.0
最愛 0.5801090999999999
飲茶 0.0
se

sent_score: 0.8519059999999999

[7]comment: 很久之前吃過的一家港式餐廳。，最近刷IG好像蠻火🔥的。，✔️雞腿排蔥油公仔麵～吃不懂？？？，✔️滑蛋什錦叉燒飯～還不錯。，🎀美食定義。見人見智。，.，.， #高雄美食 #高雄 #KAOHSIUNG #美食#LIFE #EAT，#FOOD  #TRIP #DELICIOUS #맛있다 #YUMMY #TAIWAN，#おいしい
好像 0.44268620000000003
🔥 0.139
✔ 0.27
不 -0.05
✔ 0.27
🎀 0.629
美食 0.16
定義 0.0
美食 0.16
美食 0.16
sent_score: 2.1806862000000002

[8]comment: 從大學到現在都沒有變聰明的我們😌💕難怪那麼合～偶愛泥🤟🤟，-，#高雄美食 ，#高雄港式料理 ，#崔記小餐館 ，#高雄晚餐 ，#高雄餐廳
沒 -0.1
聰明 0.46633009999999997
😌 0.48200000000000004
💕 0.1
難怪 0.7017641
美食 0.16
sent_score: 1.8100942

[9]comment: 19.10.23（水），一間屋子，住著兩個人，每天吃著三餐，就這樣過了四季。，沒有富麗堂皇，就是簡單而奢華。，，那些平凡，持續了一年，也變得不平凡。，，#KAOHSIUNG #KAOHSIUNGFOOD
沒有 -0.0921865
富麗堂皇 0.33302195
簡單 0.026052
奢華 -0.026052
平凡 -0.42478795
持續 0.0330536
變得 0.21131085
不 -0.05
平凡 -0.42478795
sent_score: -0.414376

[10]comment: 叉燒烤的剛好 不會太乾 ，肉汁保留 真的意想不到，，公仔麵搭配油蔥就是絕配
不會 -0.27884699999999996
保留 0.0
搭配 0.0289814
絕配 0.18357895
sent_score: -0.06628664999999997

[11]comment: 小叮嚀：想吃一定要訂位！不然一定排到天荒地老！還好太太有遠見，一早就訂位跟點餐！，，離家走路不用10分鐘，想吃但卻一直沒有來吃的店！！
想 0.00

🚩 -0.2
👉 0.39
最後 -0.0175984
⚠ -0.066
清楚 0.4281769
尊重 0.0
🏠 0.5
☎ 0.0
⌚ 0.2
⌚ 0.2
❌ 0.271
⚠ -0.066
外食 0.0
⚠ -0.066
櫃檯 0.0
⚠ -0.066
歡迎 0.475
不要 -0.1
不 -0.05
喜歡 0.875
幫忙 0.2
➰ -0.091
➰ -0.091
➰ -0.091
➰ -0.091
經營 0.0702444
選擇 0.0210186
轉型 0.05
重新 0.4291423
造成 0.3694322
不 -0.05
一樣 0.0540008
低調 0.0
吸引 0.0571086
不少 0.47488919999999996
民眾 0.0
前往 0.0710186
相機食先 0.5
美味 0.6096725000000001
美食 0.16
sent_score: 5.360105699999999

[103]comment: 我喜歡😋，帶鵝子打完預防針💉，當然要來吃好吃的崔記啊，（好辛苦 ）#替自己加油，，#崔記茶餐廳 #高雄#高雄美食
喜歡 0.875
😋 0.25
💉 0.358
當然 0.33799575
好吃 0.37684395
辛苦 0.0
自己 0.0
加油 0.012536499999999999
美食 0.16
sent_score: 2.3703762

[104]comment: 我的老天鵝🦢，冰火菠蘿油原來這麼好吃🥰，我以前吃的那幾家冰火菠蘿油是在鬧嗎？！🤪，流沙西多士完全正中紅心🎯，我完全愛上她了❤️，滑蛋～～～好好好吃喔👍🏻，我問合子滑蛋為什麼這麼好吃？，他說不要問妳會怕哈哈哈哈哈🤣，黯然銷魂飯自製叉燒好吃👍🏻，套餐的煲湯很好喝，用大骨熬煮又有蔬菜清甜淡淡的味道👍🏻，崔記小餐館推推推👏🏻👏🏻👏🏻，💗💗💗馬可舒芙茶讓我置入行銷一下💗💗💗，#高雄美食 #高雄美食地圖 #KAOHSIUNGFOOD #流沙西多士 #西多士 #冰火菠蘿油 #黯然銷魂飯 #滑蛋牛肉飯 #檸檬茶 #崔記小餐館
天鵝 0.0
原來 0.0
好吃 0.37684395
🥰 0.25
完全 0.45943999999999996
正中 0.0
完全 0.45943999999999996
愛上 0.54294525
❤ 0.746
好吃 0.


[0]comment: 高師父，港味
sent_score: 0

[1]comment: 吃太快@只剩菜單
只剩 -0.1
sent_score: -0.1

[2]comment: 金莎蝦球好好味
sent_score: 0

[3]comment: 超厲害的港式蛋塔😍，送上來還是熱的❤️
厲害 0.2
😍 0.6779999999999999
還是 0.1
❤ 0.746
sent_score: 1.7239999999999998

[4]comment: 聽說很正宗的港式點心...🤤🤤
聽說 0.0870222
🤤 0.15
🤤 0.15
sent_score: 0.3870222

[5]comment: NIGHT SCENES OF KAOHSIUNG #TAIWAN #台湾  #🇹🇼 #BEAUTIFUL  #BESTESTAWARD #THESHOTLIFE #ARCHITECTURE #ARCHITECTUREPORN #COLORFUL #ARCHITECTUREWATCH  #ARCHITECTURELOVERS #ARCHITECTURELIFE #MODERNARCHITECTURE #高雄 @NANCY9700
🇹 0.579
🇼 0.33299999999999996
sent_score: 0.9119999999999999

[6]comment: 肉很厲害～補補！
厲害 0.2
sent_score: 0.2

[7]comment: 天氣冷來飲茶
飲茶 0.0
sent_score: 0.0

[8]comment: #歪歪收集癖 ，#JING的美食人生
收集 0.0424385
美食 0.16
sent_score: 0.2024385

[9]comment: 😋
😋 0.25
sent_score: 0.25

[10]comment: 美味しい點心にプーアール茶、壁にはMTRマップ…台湾なのに香港を満喫してしまったわ。  #台湾  #台湾グルメ #高雄 #高雄グルメ #港式點心 #わんぱに高雄さすらいの旅2019
美味 0.6096725000000001
sent_score: 0.6096725000000001

[11]comment: CP值超高的港式點心餐廳🥢，捷運三號出口就是了，超方便，老闆娘人超好

生日 0.0
sent_score: 1.056893525

[61]comment: 初三睡到飽⁣，所以我很真誠地跟隨習俗睡到自然醒 ☺️⁣，然後開啟廢物妹妹模式⁣，穿著我心愛的米奇⁣，和沒有近視之後突然愛上的眼鏡⁣，去吃免費的好吃烤鴨 ⁣，虧我之前那麼認真減肥⁣，結果過年完全大破戒 😬⁣，只好過完年更認真減肥⁣，⁣，吃飽逛個街還被事實暴力⁣，「你沒有選擇障礙，你只是沒有錢買」🙃⁣，有道理到我不知道怎麼反駁呢哈哈哈⁣，⁣，而且連假怎麼一轉眼就剩兩天了⁣，武漢肺炎怎麼一轉眼就五個確診了⁣，這世界真是不友善 😭⁣，但看到路上有六七成的人都有戴口罩又稍稍安心了一點⁣，希望確診案例不要再升了啊…⁣，⁣，#連假倒數 #不想上班 #只想耍廢 #EATING #DIETWHATDIET #LIFE #HOLIDAY #DAILY #팩트폭력
自然 0.1455102
☺ 0.657
開啟 0.1662332
廢物 -0.43000900000000003
妹妹 0.0
心愛 0.7554457
沒有 -0.0921865
近視 -0.19585785
突然 0.0
愛上 0.54294525
免費 0.0264712
好吃 0.37684395
虧 -0.1
認真 0.5221302
完全 0.45943999999999996
😬 0.19399999999999998
只好 -0.3926862
認真 0.5221302
事實 0.47572115
暴力 -0.1262943
沒有 -0.0921865
選擇 0.0210186
障礙 0.0
只是 0.0
沒有 -0.0921865
道理 0.6399749
不 -0.05
知道 0.529169
反駁 0.0
不 -0.05
友善 0.59601625
😭 -0.09300000000000001
看到 0.0445837
口罩 0.0
安心 0.7522453
希望 0.3651647
不要 -0.1
不想 -0.2043558
只想 0.1261116
sent_score: 5.899392450000001

[62]comment: 吃鴨也可以性感 （我是說鴨很性感，，想入非非的美味 請到 #鴨寮街 ，#烤鴨 #悅城廣場 #港式飲茶
可以 0.1551797
性感 0.3019742
性感 0.3019742

# Extend antusd

In [973]:
def remove_punctuation(line):
    punctuation = "·*$,~-:!。; ！？｡＂＃＄％＆＇（）＊＋，－/\／：；＜＝＞#＠［＼］＾＿｀｛｜｝～()｟｠｢｣､、〃》「」『』【】〔〕〖〗〘〙〚〛〜〝〞〟〰〾〿–—‘'‛“”„‟…‧﹏."
    punctuation = [i for i in punctuation] + ['\n','--','☆','⋯','..','┈']
    line = [word for word in line if word not in punctuation and not word.isdigit()]

    return line

In [363]:
#====== word segment ======
'''read every file in google_review'''
all_reviews = []       # include 1~5 stars review
for filename in os.listdir('mac_extended_dict/google_review/'):              
    with open('mac_extended_dict/google_review/'+filename, newline='') as f: # open in readonly mode
        rows = csv.reader(f)
        firstline = True
        for post in rows:           # read each user post
           
            if firstline == True:   # skip fisrt line
                firstline = False
                continue
            tmp_star = int(post[2].strip()[0])
            tmp_review = post[3].strip().replace('(由 Google 提供翻譯)','').replace('(原始評論)','')
            if tmp_review == '':    # skip empty review
                continue
            all_reviews.append([tmp_star,tmp_review]) # extract star & review
            

all_reviews = np.array(all_reviews)



In [375]:
#====== filter new extended antusd words ======
def filter_new_ntusd_word(antusd, all_reviews):
    extended_antusd_word = []
    antusd_list = list(antusd['Word'])
    load_new_jeiba_word()
    new_extend_word = []
    for one_review in all_reviews[:,1]:               # get each review
        one_review = one_review.upper()
        one_review = one_review.replace('.','')
        one_review = one_review.replace(' ','')

        if one_review.find('C/P') != -1:              # found C/P => CP
            one_review = one_review.replace('/','')

        for word in remove_punctuation(jieba.lcut(one_review)): # get each word
            if word not in antusd_list and len(word) > 1:       # filter not in antusd & get rid of single letter
                extended_antusd_word.append(word)

#     print(len(extended_antusd_word))
    return extended_antusd_word

In [394]:
#====== get 5 star and 1 star review  ======
five_star_review, one_star_review, = [],[]
for one_review in all_reviews:
    if one_review[0] == '5':
        five_star_review.append(list(one_review))
    elif one_review[0] == '1':
        one_star_review.append(list(one_review))
        
        
five_star_review = np.array(five_star_review)
one_star_review = np.array(one_star_review)
print(len(five_star_review),len(one_star_review))
        

8732 1712


In [399]:
# get pos words & neg words from 5 star & 1 star review 
pos_words = filter_new_ntusd_word(antusd, five_star_review)
neg_words = filter_new_ntusd_word(antusd, one_star_review)

In [471]:
print('new negative words:',len(neg_words),'\nnew positive words:',len(pos_words))

new negative words: 19218 
new positive words: 70511


In [420]:
# count_pos_words = Counter(pos_words).most_common()
# output_csv('Count_pos_word',count_pos_words,'w') # don't execute
# count_neg_words = Counter(neg_words).most_common()
# output_csv('Count_neg_word',count_neg_words,'w') # don't execute

In [422]:
def get_noted_word(filename):
    noted_word = []
    with open(filename,newline='') as f:
        rows = csv.reader(f)
        for row in rows:
            if len(row) == 3:
                noted_word.append(row)
#                 print(row)
                
    return noted_word

new_antusd_pos_word = get_noted_word('Count_pos_word')
print(len(new_antusd_pos_word))

708


In [473]:
new_antusd_neg_word = get_noted_word('Count_neg_word')
print(len(new_antusd_neg_word))

314


In [681]:
#====== build new antusd word & senti score ======
# don't execute
# new_antusd_neg_word_senti = []
# for word_list in new_antusd_neg_word:
#     word = word_list[0]
#     new_antusd_neg_word_senti.append([word,-0.1])
    
# output_csv('new_antusd_neg_word_senti',new_antusd_neg_word_senti,'w')

# new_antusd_pos_word_senti = []
# for word_list in new_antusd_pos_word:
#     word = word_list[0]
#     new_antusd_pos_word_senti.append([word,0.2])
    
# output_csv('new_antusd_pos_word_senti',new_antusd_pos_word_senti,'w')

In [682]:
new_antusd_neg_word_senti

[['超差', -0.1],
 ['太貴', -0.1],
 ['蟑螂', -0.1],
 ['死鹹', -0.1],
 ['拉肚子', -0.1],
 ['送錯', -0.1],
 ['不推', -0.1],
 ['再也不會', -0.1],
 ['軟爛', -0.1],
 ['味精', -0.1],
 ['沒吃過', -0.1],
 ['幹嘛', -0.1],
 ['不怎麼樣', -0.1],
 ['老鼠', -0.1],
 ['差到', -0.1],
 ['吃不飽', -0.1],
 ['CP值低', -0.1],
 ['趕人', -0.1],
 ['態度惡劣', -0.1],
 ['高估', -0.1],
 ['這麼久', -0.1],
 ['CP值超低', -0.1],
 ['無言', -0.1],
 ['收走', -0.1],
 ['很難吃', -0.1],
 ['很髒', -0.1],
 ['臉色', -0.1],
 ['不給', -0.1],
 ['零分', -0.1],
 ['濃鬱', -0.1],
 ['沒多好吃', -0.1],
 ['太爛', -0.1],
 ['再也', -0.1],
 ['太軟', -0.1],
 ['面對面', -0.1],
 ['要不要', -0.1],
 ['沒洗', -0.1],
 ['超爛', -0.1],
 ['沒來', -0.1],
 ['腥味', -0.1],
 ['要命', -0.1],
 ['不優', -0.1],
 ['不敢恭維', -0.1],
 ['一星', -0.1],
 ['咳嗽', -0.1],
 ['薄薄的', -0.1],
 ['很薄', -0.1],
 ['大吼大叫', -0.1],
 ['下嚥', -0.1],
 ['超貴', -0.1],
 ['歐巴桑', -0.1],
 ['不太好', -0.1],
 ['差太多', -0.1],
 ['敷衍', -0.1],
 ['不來', -0.1],
 ['漏單', -0.1],
 ['CP值很低', -0.1],
 ['有點鹹', -0.1],
 ['聽不懂', -0.1],
 ['差差', -0.1],
 ['超久', -0.1],
 ['還被', -0.1],
 ['小聲', -0.1],
 ['地上', -0.1],
 ['到極點'

# combine csv

In [317]:
article1 = pd.read_csv('dataset/ig_article/store_article/pasta/article_MIGA KITCHEN PASTA.csv')
article2 = pd.read_csv('dataset/ig_article/store_article/pasta/article_米家廚房.csv')
combined_article = pd.concat([article1, article2], ignore_index=True)
combined_article.to_csv('dataset/ig_article/store_article/pasta/article_MIGA KITCHEN PASTA_米家廚房.csv')

# extend dictionary

In [413]:
# extend dictionary
word_to_weight = {
    "土地公": 1,
    "土地婆": 1,
    "公有": 2,
    "緯來體育台": 1,
    "鬼金棒": 3,
    "海底撈": 5
}
dictionary = construct_dictionary(word_to_weight)
print(dictionary)

[(2, {'公有': 2.0}), (3, {'土地公': 1.0, '土地婆': 1.0, '鬼金棒': 3.0, '海底撈': 5.0}), (5, {'緯來體育台': 1.0})]


# Scrape url via selenium

In [155]:
store_selenium_param = get_selenium_param('selenium_url')
store_names = []
store_page_xpath = []
first_page_xpath = []

for line in store_selenium_param:
    store_names.append(line[0])
    store_page_xpath.append(line[1])
    first_page_xpath.append(line[2])

    
print(first_page_xpath)
# store_names = [store_selenium_param[0][0]]
# store_page_xpath = [store_selenium_param[0][1]]
# first_page_xpath = [store_selenium_param[0][2]]
# get_page_count = [4000]
# print(first_page_xpath)

['href="/p/B_PgFUaDk2y/"', 'href="/p/B_RlyLqA0z8/"', 'href="/p/B_SHtKjJof5/"']


In [156]:
#===== scrape url from first post ======
startTime = time.time()

#====== use selenium to crawl store url ======
from selenium import webdriver

ig_home = "https://instagram.com"
driver = webdriver.Chrome(executable_path="chromedriver_linux64/chromedriver") # Use Chrome
driver.get(ig_home) # open ig home page
time.sleep(2)

# login
driver.find_element_by_xpath('//input[@name="username"]').send_keys('bestronger10142008')
driver.find_element_by_xpath('//input[@name="password"]').send_keys('igcoke1231')
time.sleep(2)
driver.find_element_by_xpath('//button[@type="submit"]').click()
time.sleep(5)

# iterate to get each store url
for store_index in range(len(store_names)):
    # input store name
    driver.find_element_by_xpath('//input[@type="text"]').send_keys(store_names[store_index]) 
    time.sleep(5)
    
    # driver.find_element_by_xpath('//a[@href="/explore/tags/雞吉君拉麵/"]').click() # click store page
    driver.find_element_by_xpath('//a[@' + store_page_xpath[store_index] + ']').click() # click store page
    time.sleep(5)
    
    # driver.find_element_by_xpath('//a[@href="/p/B-CEZjVl8GC/"]').click() # click first page link
    driver.find_element_by_xpath('//a[@' + first_page_xpath[store_index] + ']').click() # click first page link
    time.sleep(3)

    # get url of current page
    url_list, post_date = [], []
    url_list.append([driver.current_url]) # get first page url
    time.sleep(1)
    post_date.append([driver.find_element_by_xpath('//time[@class="_1o9PC Nzb55"]').text])
    time.sleep(3)

    # get 500 page url
#     flag = 0
#     for i in range(get_page_count[store_index]):
    for i in range(8000):
        if check_exists_by_xpath('//a[@tabindex="0"][2]'):
            driver.find_element_by_xpath('//a[@tabindex="0"][2]').click()
        else:
            break

        time.sleep(1)
        url_list.append([driver.current_url])
        time.sleep(5)
        post_date.append([driver.find_element_by_xpath('//time[@class="_1o9PC Nzb55"]').text])
        stopDate = post_date[-1][0]
#         print(post_date[-1][0],type(post_date[-1][0]))
        
        # stop date = 2019.6.1
        if stopDate[:stopDate.find('年')] == '2019' and stopDate[stopDate.find('年')+1:stopDate.find('月')] == '5':
            break
            
    ActionChains(driver).send_keys(Keys.ESCAPE).perform() # close floating page
    output_csv('dataset/ig_article/store_url/url_' + store_names[store_index], url_list, 'w+')
    output_csv('dataset/ig_article/store_url/date_' + store_names[store_index], post_date, 'w+')
    print(store_names[store_index]+'finished!')
    
driver.close()
stopTime = time.time()
print(stopTime-startTime/60)

HUN 混finished!
MINT Pasta 義大利麵finished!
JAI 宅finished!
1561167483.6183445


In [40]:
#===== scrape url from assigned date ======
startTime = time.time()

#====== use selenium to crawl store url ======
from selenium import webdriver

ig_home = "https://instagram.com"
driver = webdriver.Chrome(executable_path="chromedriver_linux64/chromedriver") # Use Chrome
driver.get(ig_home) # open ig home page
time.sleep(2)

# login
driver.find_element_by_xpath('//input[@name="username"]').send_keys('bestronger10142008')
driver.find_element_by_xpath('//input[@name="password"]').send_keys('igcoke1231')
time.sleep(2)
driver.find_element_by_xpath('//button[@type="submit"]').click()
time.sleep(5)

# iterate to get each store url
for store_index in range(len(store_names)):
    # input store name
    driver.find_element_by_xpath('//input[@type="text"]').send_keys(store_names[store_index]) 
    time.sleep(4)
    
    # driver.find_element_by_xpath('//a[@href="/explore/tags/雞吉君拉麵/"]').click() # click store page
    driver.find_element_by_xpath('//a[@' + store_page_xpath[store_index] + ']').click() # click store page
    time.sleep(5)
    
    # driver.find_element_by_xpath('//a[@href="/p/B-CEZjVl8GC/"]').click() # click first page link
    driver.find_element_by_xpath('//a[@' + first_page_xpath[store_index] + ']').click() # click first page link
    time.sleep(4)

    # get url of current page
    url_list, post_date, output_post_date = [], [], []
    post_date.append([driver.find_element_by_xpath('//time[@class="_1o9PC Nzb55"]').text]) # get first page date

    # get 500 page url
    for i in range(5000):
        
        stopDate = post_date[-1][0]
        
        if stopDate[:stopDate.find('年')] != '2019':
#             print(stopDate)
            
            if check_exists_by_xpath('//a[@tabindex="0"][2]'):
                driver.find_element_by_xpath('//a[@tabindex="0"][2]').click() # click next page
                time.sleep(3)
            else:
                break
            time.sleep(1)
            post_date.append([driver.find_element_by_xpath('//time[@class="_1o9PC Nzb55"]').text])
            continue
            
            
#         time.sleep(1)
        url_list.append([driver.current_url])
        time.sleep(1)
        temp_date = [driver.find_element_by_xpath('//time[@class="_1o9PC Nzb55"]').text]
        post_date.append(temp_date)
        output_post_date.append(temp_date)
        
        if check_exists_by_xpath('//a[@tabindex="0"][2]'):
            driver.find_element_by_xpath('//a[@tabindex="0"][2]').click() # click next page
            time.sleep(4)
        else:
            break

        # stop date = 2019.6.1
        if stopDate[:stopDate.find('年')] == '2019' and stopDate[stopDate.find('年')+1:stopDate.find('月')] == '5':
            break
        
            
    ActionChains(driver).send_keys(Keys.ESCAPE).perform() # close floating page
    output_csv('dataset/ig_article/store_url/url_' + store_names[store_index], url_list[:-1], 'w+')
    output_csv('dataset/ig_article/store_url/date_' + store_names[store_index], output_post_date[:-1], 'w+')
    print(store_names[store_index]+'finished!')
    
driver.close()
stopTime = time.time()
print((stopTime-startTime)/60)

新馬辣武昌店finished!
新馬辣經典馬辣鍋finished!
青花驕麻辣鍋板橋縣民大道店finished!
馬辣頂級麻辣鴛鴦火鍋-中山店finished!
馬辣頂級麻辣鴛鴦火鍋 漢口店finished!
問鼎麻辣鍋忠孝店finished!
問鼎 麻辣鍋 養生鍋 粉絲俱樂部finished!
滿堂紅-松江店finished!
滿堂紅bellavita店finished!
153.04108297030132


In [259]:
# teststr = '2019年8月10日'
teststr = '3月23日'
if teststr[:teststr.find('年')] == '2019' and teststr[teststr.find('年')+1:teststr.find('月')] == '8':
    print('yes')